In [1]:
import folium as fm
import pandas as pd
import numpy as np
import geopandas as gpd
from shapely.geometry import Point, Polygon
from fiona.drvsupport import supported_drivers
import panel as pn
from fastkml.kml import KML
import matplotlib.pyplot as plt
pn.extension(sizing_mode="stretch_width")

1. Read file into memory

In [3]:
#these first blocks are just so you guys can see what I did to get the zipcode layer built
#kml downloaded from https://www2.census.gov/geo/tiger/GENZ2020/kml/cb_2020_us_zcta520_500k.zip
#I didn't commit the full file because it is too big for github
supported_drivers['KML'] = 'rw'
zip_geography = gpd.read_file('./cb_2020_us_zcta520_500k.kml', driver='KML')

DriverError: ./cb_2020_us_zcta520_500k.kml: No such file or directory

In [ ]:
zip_geography.info()

In [4]:
#reads state boundries for the US so that I can filter out just DC, MD, and VA zips.
supported_drivers['KML'] = 'rw'
state_geography = gpd.read_file('./cb_2020_us_state_500k.kml', driver='KML')
state_geography

DriverError: ./cb_2020_us_state_500k.kml: No such file or directory

Chris Smith, replicate the above read in for the three 'places' kml files and concat like below to produce your geodataframe that you will add your metric series column to.

In [48]:
project_zips = gpd.GeoDataFrame()
dc_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[10].geometry)]
md_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[23].geometry)]
va_zips = zip_geography[zip_geography.geometry.within(state_geography.loc[51].geometry)]
project_zips = pd.concat([dc_zips, md_zips, va_zips])
project_zips.to_file('DC_MD_VA_Zipcodes.kml', driver = 'KML') #saves df to kml file

In [2]:
supported_drivers['KML'] = 'rw'
project_zips = gpd.read_file('./Geographies/DC_MD_VA_Zipcodes.kml', driver='KML')

In [3]:
project_zips.head()

Name  \
0  <at><openparen>20001<closeparen>   
1  <at><openparen>20002<closeparen>   
2  <at><openparen>20003<closeparen>   
3  <at><openparen>20004<closeparen>   
4  <at><openparen>20005<closeparen>   

                                         Description  \
0  <center><table><tr><th colspan='2' align='cent...   
1  <center><table><tr><th colspan='2' align='cent...   
2  <center><table><tr><th colspan='2' align='cent...   
3  <center><table><tr><th colspan='2' align='cent...   
4  <center><table><tr><th colspan='2' align='cent...   

                                            geometry  
0  POLYGON Z ((-77.02758 38.90964 0.00000, -77.02...  
1  POLYGON Z ((-77.01217 38.89209 0.00000, -77.01...  
2  POLYGON Z ((-77.01402 38.88236 0.00000, -77.01...  
3  POLYGON Z ((-77.03365 38.89735 0.00000, -77.03...  
4  POLYGON Z ((-77.03654 38.90252 0.00000, -77.03...

You need to add a series column to the above geodataframe that has the associated value for your metric for each zipcode geography. (if using zip codes as your map layer area boundry.

In [4]:
#Point takes long then lat
pentagon = (38.8719570149196, -77.05630981703996)
pentagon_grid = Point(pentagon[1],pentagon[0])

In [5]:
#Once you have your metric loaded on your GeoDataFrame above, you can use the code below to start 
#to visualize. We will work more on the fillcolor and popups later.
zip_map = fm.Map(location=pentagon, zoom_start=12, tiles='CartoDB positron')
fm.Marker(pentagon, popup = 'Pentagon').add_to(zip_map)
for _, r in project_zips.iterrows():
    # Without simplifying the representation of each borough,
    # the map might not be displayed
    sim_geo = gpd.GeoSeries(r['geometry']).simplify(tolerance=0.001)
    geo_j = sim_geo.to_json()
    geo_j = fm.GeoJson(data=geo_j,
                           style_function=lambda x: {'fillColor': 'orange'})
    fm.Popup(r['Description']).add_to(geo_j)
    geo_j.add_to(zip_map)
zip_map